In [3]:
import folium
import json

import numpy as np
import pandas as pd

from folium.plugins import HeatMap, HeatMapWithTime
# from geopy.geocoders import Nominatim
from tqdm import tqdm

In [4]:
def has_number(s):

    if (isinstance(s, float)):

        return False

    return any(c.isdigit() for c in s)

def collect_parsed_locations():

    parsed = set()

    try:

        with open("coordinates.jsonl", "r") as infile:

            for line in infile:

                ex = json.loads(line.strip())
                parsed.add(ex["location"])

    except (FileNotFoundError):

        pass

    return parsed

def collect_good_keys():

    good_keys = set()

    try:

        with open("coordinates.jsonl", "r") as infile:

            for line in infile:

                ex = json.loads(line.strip())
                good_keys.add(ex["location"])

    except (FileNotFoundError):

        pass

    return good_keys

def lat_long_dicts():

    lat_dict = {None : None}
    long_dict = {None : None}

    with open("coordinates.jsonl", "r") as infile:

        for line in infile:

            ex = json.loads(line.strip())

            key = ex["location"]
            latitude = ex["coordinates"][0]
            longitude = ex["coordinates"][1]
            lat_dict[key] = latitude
            long_dict[key] = longitude

    return lat_dict, long_dict

In [3]:
# geolocator = Nominatim(
#     domain = "nominatim:8080",
#     scheme = "http",
#     user_agent = "geolocator",
# )

In [7]:
dtypes = {
    "tag_number_masked" : str,
    "date_of_infraction" : str,
    "infraction_code" : "category",
    "infraction_description" : str,
    "set_fine_amount" : float,
    "time_of_infraction" : str,
    "location1" : str,
    "location2" : str,
    "location3" : str,
    "location4" : str,
    "province" : "category",
    "datetime_of_infraction" : str,
    "date_of_infraction_dt" : str,
    "time_of_infraction_dt" : str,
    "year_of_infraction" : "category",
    "month_of_infraction" : "category",
    "day_of_infraction" : "category",
    "dayofweek_infraction" : "category",
}
data = pd.read_csv("parking.csv", dtype = dtypes)

In [48]:
day_dict = {k : v for k, v in zip(["0.0", "1.0", "2.0", "3.0", "4.0", "5.0", "6.0"], ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"])}
month_dict = {k : v for k, v in zip(["1.0", "2.0", "3.0", "4.0", "5.0", "6.0", "7.0", "8.0", "9.0", "10.0", "11.0", "12.0"], ["January", "February", "March", "April", "May", "June", "July", "August", "September", "October", "November", "December"])}

# hours = [f"{i}.0" for i in range(0, 24)]
hours = [i for i in range(0, 24)]

In [5]:
#parsed = collect_parsed_locations()

#collected1 = 0
#collected2 = 0

#with open("../data/coordinates.jsonl", "a") as outfile:
    
#    for loc in tqdm(set(data[data.location2.map(has_number)].location2) | set(data[data.location2.isna() & data.location4.map(has_number)].location4)):

#        loc = " ".join(loc.split())

#        if (loc in parsed):

#            continue
        
#        location = geolocator.geocode(loc + ", Toronto, Ontario, Canada")
        
#        if (location is not None):
            
#            ex = {
#                "location" : loc,
#                "coordinates" : [location.latitude, location.longitude]
#            }

#            outfile.write(json.dumps(ex) + "\n")
#            parsed.add(loc)
#            collected1 += 1

#    for _, row in tqdm(data[(~data.location2.isna()) & (~data.location2.map(has_number)) & (~data.location4.isna())].iterrows()):

#        loc1 = " ".join(row.location2.split())
#        loc2 = " ".join(row.location4.split())
#        loc = ", ".join(sorted([loc1, loc2]))

#        if (loc in parsed):

#            continue

#        location1 = geolocator.geocode(f"{loc1}, {loc2}, Toronto, Ontario, Canada")
#        location2 = geolocator.geocode(f"{loc2}, {loc1}, Toronto, Ontario, Canada")

#        parsed.add(loc)

#        if (location1 is not None):

#            ex = {
#                "location" : loc,
#                "coordinates" : [location1.latitude, location1.longitude]
#            }

#        elif (location2 is not None):

#            ex = {
#                "location" : loc,
#                "coordinates" : [location2.latitude, location2.longitude]
#            }

#        else:

#            continue

#        outfile.write(json.dumps(ex) + "\n")
#        collected2 += 1

#print()
#print(f"collected {collected1} from part 1")
#print(f"collected {collected2} from part 2")
#print()

In [9]:
good_keys = collect_good_keys()

data["latitude"] = [None] * len(data)

data.loc[data.location2.map(has_number), "latitude"] = data.loc[data.location2.map(has_number), "location2"].str.split().str.join(" ")
data.loc[data.location2.isna() & data.location4.map(has_number), "latitude"] = data.loc[data.location2.isna() & data.location4.map(has_number), "location4"].str.split().str.join(" ")
data.loc[(~data.location2.isna()) & (~data.location2.map(has_number)) & (~data.location4.isna()), "latitude"] = (data[(~data.location2.isna()) & (~data.location2.map(has_number)) & (~data.location4.isna())].location2.str.split().str.join(" ") + ", " + data[(~data.location2.isna()) & (~data.location2.map(has_number)) & (~data.location4.isna())].location4.str.split().str.join(" ")).str.split(", ").map(sorted).str.join(", ")
data.loc[~data.latitude.isin(good_keys), "latitude"] = None
data["longitude"] = data["latitude"]

data[~data.latitude.isna()]

tag_number_masked date_of_infraction infraction_code  \
0                 ***51471           20191124           207.0   
1                 ***61170           20191124           207.0   
2                 ***92224           20191124           207.0   
4                 ***39600           20191124             2.0   
5                 ***63128           20191124           355.0   
...                    ...                ...             ...   
40022005          ***34252           20220422             3.0   
40022006          ***80771           20220422             2.0   
40022007          ***68521           20220422             2.0   
40022009          ***80772           20220422             2.0   
40022010          ***68522           20220422             2.0   

                  infraction_description  set_fine_amount time_of_infraction  \
0         PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
1         PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
2         PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
4             PARK - LONGER THAN 3 HOURS             30.0               2012   
5           PARK IN ACCESSIBLE NO PERMIT            450.0               2013   
...                                  ...              ...                ...   
40022005        PARK ON PRIVATE PROPERTY             30.0               0437   
40022006      PARK - LONGER THAN 3 HOURS             30.0               0437   
40022007      PARK - LONGER THAN 3 HOURS             30.0               0437   
40022009      PARK - LONGER THAN 3 HOURS             30.0               0439   
40022010      PARK - LONGER THAN 3 HOURS             30.0               0439   

         location1              location2 location3 location4 province  \
0               NR       548 DANFORTH AVE       NaN       NaN       ON   
1               NR         510 COLLEGE ST       NaN       NaN       ON   
2               NR  541 MOUNT PLEASANT RD       NaN       NaN       ON   
4               NR        32 FIELDWOOD DR       NaN       NaN       ON   
5               AT       555 REXDALE BLVD       NaN       NaN       ON   
...            ...                    ...       ...       ...      ...   
40022005        AT   225 VILLAGE GREEN SQ       NaN       NaN       ON   
40022006        NR     51 TRAILRIDGE CRES       NaN       NaN       ON   
40022007       OPP    504 RUSSELL HILL RD       NaN       NaN       ON   
40022009        NR     39 TRAILRIDGE CRES       NaN       NaN       ON   
40022010       OPP    470 RUSSELL HILL RD       NaN       NaN       ON   

         datetime_of_infraction date_of_infraction_dt time_of_infraction_dt  \
0                  201911242011            2019-11-24   1900-01-01 20:11:00   
1                  201911242011            2019-11-24   1900-01-01 20:11:00   
2                  201911242011            2019-11-24   1900-01-01 20:11:00   
4                  201911242012            2019-11-24   1900-01-01 20:12:00   
5                  201911242013            2019-11-24   1900-01-01 20:13:00   
...                         ...                   ...                   ...   
40022005           202204220437            2022-04-22   1900-01-01 04:37:00   
40022006           202204220437            2022-04-22   1900-01-01 04:37:00   
40022007           202204220437            2022-04-22   1900-01-01 04:37:00   
40022009           202204220439            2022-04-22   1900-01-01 04:39:00   
40022010           202204220439            2022-04-22   1900-01-01 04:39:00   

         year_of_infraction month_of_infraction day_of_infraction  \
0                    2019.0                11.0              24.0   
1                    2019.0                11.0              24.0   
2                    2019.0                11.0              24.0   
4                    2019.0                11.0              24.0   
5                    2019.0                11.0              24.0   
...            

In [10]:
lat_dict, long_dict = lat_long_dicts()

data["latitude"] = data.latitude.map(lambda x : lat_dict[x])
data["longitude"] = data.longitude.map(lambda x : long_dict[x])

In [8]:
# data.to_csv("../data/parking_with_position.csv", index = False)

In [11]:
len(data[~data.latitude.isna()]) / len(data), len(data[data.latitude.isna()]) / len(data)

(0.6771462833289411, 0.32285371667105883)

In [12]:
print(data.latitude.min(), data.latitude.max())
print(data.longitude.min(), data.longitude.max())

43.586386 43.853205
-79.63746402342602 -79.1222408


In [13]:
#lat_space = data.latitude.quantile(q = np.linspace(0, 1, 41)).values
#long_space = data.longitude.quantile(q = np.linspace(0, 1, 41)).values

lat_space = 40
long_space = 50

data["lat_bucket"] = pd.cut(data.latitude, bins = lat_space, right = False, labels = None, retbins = False)
data["long_bucket"] = pd.cut(data.longitude, bins = long_space, right = False, labels = None, retbins = False)

In [126]:
g = data.groupby(by = ["year_of_infraction", "month_of_infraction", "day_of_infraction", "lat_bucket", "long_bucket"], observed = True).agg("count")["tag_number_masked"].rename({"tag_number_masked" : "count"}).reset_index()

In [127]:
g.year_of_infraction = g.year_of_infraction.astype(float)
g.month_of_infraction = g.month_of_infraction.astype(float)
g.day_of_infraction = g.day_of_infraction.astype(float)
g.sort_values(by = ["year_of_infraction", "month_of_infraction", "day_of_infraction"])

year_of_infraction  month_of_infraction  day_of_infraction  \
1827783              2009.0                  1.0                1.0   
1827784              2009.0                  1.0                1.0   
1827785              2009.0                  1.0                1.0   
1827786              2009.0                  1.0                1.0   
1827787              2009.0                  1.0                1.0   
...                     ...                  ...                ...   
525405               2022.0                 12.0               31.0   
525406               2022.0                 12.0               31.0   
525407               2022.0                 12.0               31.0   
525408               2022.0                 12.0               31.0   
525409               2022.0                 12.0               31.0   

               lat_bucket         long_bucket  tag_number_masked  
1827783    [43.593, 43.6)  [-79.514, -79.504)                  1  
1827784    [43.6, 43.606)  [-79.493, -79.483)                  1  
1827785  [43.606, 43.613)  [-79.514, -79.504)                  1  
1827786   [43.613, 43.62)  [-79.504, -79.493)                  1  
1827787   [43.62, 43.626)  [-79.493, -79.483)                  1  
...                   ...                 ...                ...  
525405   [43.807, 43.813)  [-79.236, -79.225)                  1  
525406   [43.807, 43.813)  [-79.215, -79.205)                  4  
525407   [43.807, 43.813)  [-79.184, -79.174)                  1  
525408    [43.813, 43.82)  [-79.277, -79.267)                  2  
525409    [43.813, 43.82)  [-79.215, -79.205)                  6  

[2071125 rows x 6 columns]

In [14]:
lat_points = set()
long_points = set()

for r in set(data.lat_bucket):

    if (not isinstance(r, float)):

        lat_points.add(r.left)
        lat_points.add(r.right)

for r in set(data.long_bucket):

    if (not isinstance(r, float)):

        long_points.add(r.left)
        long_points.add(r.right)

lat_points = sorted(lat_points)
long_points = sorted(long_points)

In [25]:
lat = 43.6532
lon = -79.3832

min_lon, max_lon = data.longitude.min(), data.longitude.max()
min_lat, max_lat = data.latitude.min(), data.latitude.max()
zoom_start = 12

m = folium.Map(
    location = (lat, lon),
    zoom_start = zoom_start,
    max_bounds = True,
    min_lat = min_lat,
    max_lat = max_lat,
    min_lon = min_lon,
    max_lon = max_lon,
)

h_lines = []
v_lines = []

for j in range(len(lat_points)):

    lines = [[(lat_points[j], long_points[i]), (lat_points[j], long_points[i + 1])] for i in range(len(long_points) - 1)]
    h_lines.extend(lines)

for j in range(len(long_points)):
    
    lines = [[(lat_points[i], long_points[j]), (lat_points[i + 1], long_points[j])] for i in range(len(lat_points) - 1)]
    v_lines.extend(lines)

folium.PolyLine(
    locations = h_lines + v_lines,
    color = "black",
    weight = 1,
    opacity = 0.5,
    smooth_factor = 0,
).add_to(m)
m

In [26]:
# m.save("figures/toronto_grid.png")

In [16]:
g = data.groupby(by = ["lat_bucket", "long_bucket"], observed = True).agg("count").rename(columns = {"tag_number_masked" : "count"})["count"].reset_index()

points = []

g["count"] = g["count"] / g["count"].max()

for _, row in g.iterrows():

    x = float(row.lat_bucket.left + row.lat_bucket.right) / 2
    y = float(row.long_bucket.left + row.long_bucket.right) / 2
    v = row["count"]

    points.append((x, y, v))

points = np.array(points).tolist()

HeatMap(points).add_to(m)
m

In [52]:
data["hour_of_infraction"] = pd.to_datetime(data.time_of_infraction_dt).dt.hour.astype("category")

In [53]:
data.head()

tag_number_masked date_of_infraction infraction_code  \
0          ***51471           20191124           207.0   
1          ***61170           20191124           207.0   
2          ***92224           20191124           207.0   
3          ***76780           20191124            29.0   
4          ***39600           20191124             2.0   

           infraction_description  set_fine_amount time_of_infraction  \
0  PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
1  PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
2  PARK MACHINE-REQD FEE NOT PAID             30.0               2011   
3  PARK PROHIBITED TIME NO PERMIT             30.0               2012   
4      PARK - LONGER THAN 3 HOURS             30.0               2012   

  location1              location2 location3   location4  ...  \
0        NR       548 DANFORTH AVE       NaN         NaN  ...   
1        NR         510 COLLEGE ST       NaN         NaN  ...   
2        NR  541 MOUNT PLEASANT RD       NaN         NaN  ...   
3       E/S            PRINCESS ST       S/O  FRONT ST E  ...   
4        NR        32 FIELDWOOD DR       NaN         NaN  ...   

  time_of_infraction_dt year_of_infraction month_of_infraction  \
0   1900-01-01 20:11:00             2019.0                11.0   
1   1900-01-01 20:11:00             2019.0                11.0   
2   1900-01-01 20:11:00             2019.0                11.0   
3   1900-01-01 20:12:00             2019.0                11.0   
4   1900-01-01 20:12:00             2019.0                11.0   

  day_of_infraction dayofweek_infraction   latitude  longitude  \
0              24.0                  6.0  43.678510 -79.347730   
1              24.0                  6.0  43.656068 -79.410602   
2              24.0                  6.0  43.702723 -79.387794   
3              24.0                  6.0        NaN        NaN   
4              24.0                  6.0  43.824262 -79.270556   

        lat_bucket         long_bucket  hour_of_infraction  
0  [43.673, 43.68)  [-79.349, -79.339)                20.0  
1  [43.653, 43.66)    [-79.411, -79.4)                20.0  
2   [43.7, 43.706)    [-79.39, -79.38)                20.0  
3              NaN                 NaN                20.0  
4  [43.82, 43.827)  [-79.277, -79.267)                20.0  

[5 rows x 23 columns]

In [73]:
# data[data.year_of_infraction == "2019.0"]

In [35]:
revenue_by_loc = data.groupby("location2").agg({"set_fine_amount": "sum"})
revenue_by_loc["set_fine_amount"].sort_values(ascending = False)

location2
40 ORCHARD VIEW BLVD    3694730.0
410 COLLEGE ST          3616960.0
1 BRIMLEY RD S          3143985.0
18 GRENVILLE ST         2794370.0
20 EDWARD ST            2630960.0
                          ...    
CONSILIUM PLACE               0.0
186 LAUDER AV                 0.0
131 BLOOR T W                 0.0
21 NORTH TOWN WAY             0.0
10 CANISH RD                  0.0
Name: set_fine_amount, Length: 673254, dtype: float64

In [74]:
lat = 43.6532
lon = -79.3832

min_lon, max_lon = data.longitude.min(), data.longitude.max()
min_lat, max_lat = data.latitude.min(), data.latitude.max()
zoom_start = 12

m = folium.Map(
    location = (lat, lon),
    zoom_start = zoom_start,
    max_bounds = True,
    min_lat = min_lat,
    max_lat = max_lat,
    min_lon = min_lon,
    max_lon = max_lon,
)

h_lines = []
v_lines = []

for j in range(len(lat_points)):

    lines = [[(lat_points[j], long_points[i]), (lat_points[j], long_points[i + 1])] for i in range(len(long_points) - 1)]
    h_lines.extend(lines)

for j in range(len(long_points)):
    
    lines = [[(lat_points[i], long_points[j]), (lat_points[i + 1], long_points[j])] for i in range(len(lat_points) - 1)]
    v_lines.extend(lines)

folium.PolyLine(
    locations = h_lines + v_lines,
    color = "black",
    weight = 1,
    opacity = 0.5,
    smooth_factor = 0,
).add_to(m)

# infraction count
# g = data.groupby(by = ["month_of_infraction", "dayofweek_infraction", "lat_bucket", "long_bucket"], observed = True).agg("count").rename(columns = {"tag_number_masked" : "count"})["count"].reset_index()
# g["count"] = g["count"].clip(upper = 1000)

#g["count"] = (g["count"] / g["count"].max()).clip(lower = 0.25)
#g["count"] = g["count"] / g["count"].max()
# g = g[g["count"] < 1000] 

# revenue
g = data[data["year_of_infraction"] == "2020.0"]
g = data.groupby(by = ["month_of_infraction", "dayofweek_infraction", "lat_bucket", "long_bucket"], observed = True).agg({"set_fine_amount": "sum"}).rename(columns = {"set_fine_amount": "revenue"})["revenue"].reset_index()
g["revenue"] = g["revenue"].clip(upper = 50000)


index = []
time_slices = []

for month in ["1.0", "2.0", "3.0", "4.0", "5.0", "6.0", "7.0", "8.0", "9.0", "10.0", "11.0", "12.0"]:

    for day in ["0.0", "1.0", "2.0", "3.0", "4.0", "5.0", "6.0"]:

        points = []
        tmp = g[(g.dayofweek_infraction == day) & (g.month_of_infraction == month)]
#         tmp["count"] = tmp["count"] / (tmp["count"].max())
        tmp["revenue"] = tmp["revenue"] / (tmp["revenue"].max())
        
#       looks through the slice of that data that is the given day, month, whatever
#       takes each row and turn it into a triple of (lat, long, value)

        for _, row in tmp.iterrows():

            x = float(row.lat_bucket.left + row.lat_bucket.right) / 2
            y = float(row.long_bucket.left + row.long_bucket.right) / 2
            v = row["revenue"]
            
            points.append((x, y, v))
            
        index.append(f"{month_dict[month]} - {day_dict[day]}")
        
        points = np.array(points).tolist()
        time_slices.append(points)

HeatMapWithTime(time_slices, index = index).add_to(m)
m

/var/folders/sc/c663j6bx65391kdjgk7jy_d00000gn/T/ipykernel_24566/3084904434.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp["revenue"] = tmp["revenue"] / (tmp["revenue"].max())


In [76]:
lat = 43.6532
lon = -79.3832

min_lon, max_lon = data.longitude.min(), data.longitude.max()
min_lat, max_lat = data.latitude.min(), data.latitude.max()
zoom_start = 12

m = folium.Map(
    location = (lat, lon),
    zoom_start = zoom_start,
    max_bounds = True,
    min_lat = min_lat,
    max_lat = max_lat,
    min_lon = min_lon,
    max_lon = max_lon,
)

h_lines = []
v_lines = []

for j in range(len(lat_points)):

    lines = [[(lat_points[j], long_points[i]), (lat_points[j], long_points[i + 1])] for i in range(len(long_points) - 1)]
    h_lines.extend(lines)

for j in range(len(long_points)):
    
    lines = [[(lat_points[i], long_points[j]), (lat_points[i + 1], long_points[j])] for i in range(len(lat_points) - 1)]
    v_lines.extend(lines)

folium.PolyLine(
    locations = h_lines + v_lines,
    color = "black",
    weight = 1,
    opacity = 0.5,
    smooth_factor = 0,
).add_to(m)

# infraction count
# g = data.groupby(by = ["month_of_infraction", "dayofweek_infraction", "lat_bucket", "long_bucket"], observed = True).agg("count").rename(columns = {"tag_number_masked" : "count"})["count"].reset_index()
# g["count"] = g["count"].clip(upper = 1000)

# revenue
# month of the year - day of the week
# g = data.groupby(by = ["month_of_infraction", "dayofweek_infraction", "lat_bucket", "long_bucket"], observed = True).agg({"set_fine_amount": "sum"}).rename(columns = {"set_fine_amount": "revenue"})["revenue"].reset_index()
# day of the week - time of the day
g = data.groupby(by = ["dayofweek_infraction", "hour_of_infraction", "lat_bucket", "long_bucket"], observed = True).agg({"set_fine_amount": "sum"}).rename(columns = {"set_fine_amount": "revenue"})["revenue"].reset_index()
g["revenue"] = g["revenue"].clip(upper = 5000)


index = []
time_slices = []

for day in ["0.0", "1.0", "2.0", "3.0", "4.0", "5.0", "6.0"]:

    for time in hours:

        points = []
        tmp = g[(g.hour_of_infraction == time) & (g.dayofweek_infraction == day)]
#         tmp["count"] = tmp["count"] / (tmp["count"].max())
        tmp["revenue"] = tmp["revenue"] / (tmp["revenue"].max())
        
#       looks through the slice of that data that is the given day, month, whatever
#       takes each row and turn it into a triple of (lat, long, value)

        for _, row in tmp.iterrows():

            x = float(row.lat_bucket.left + row.lat_bucket.right) / 2
            y = float(row.long_bucket.left + row.long_bucket.right) / 2
            v = row["revenue"]
            
            points.append((x, y, v))
            
        index.append(f"{day_dict[day]} - hour: {time}")
        
        points = np.array(points).tolist()
        time_slices.append(points)

HeatMapWithTime(time_slices, index = index).add_to(m)
m

/var/folders/sc/c663j6bx65391kdjgk7jy_d00000gn/T/ipykernel_24566/628984813.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp["revenue"] = tmp["revenue"] / (tmp["revenue"].max())
